<a href="https://colab.research.google.com/github/paritoshkc/TextAnalytics/blob/master/Review_Scrapping.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [0]:
import requests
import urllib.request
import time
from bs4 import BeautifulSoup
import lxml.html as lh
import pandas as pd
import re



# Get movie name and year list from wikipedia 
url_wiki='https://en.wikipedia.org/wiki/List_of_Academy_Award-winning_films'
#Create a handle, page, to handle the contents of the website
page = requests.get(url_wiki).text
soup= BeautifulSoup(page, "lxml")

My_table = soup.find('table',{'class':'wikitable sortable'})
links = My_table.find_all('a')

# for future use
name=[]
year=[]


# used for constrcution of urls
url_front = 'https://www.rottentomatoes.com/m/'
url_back_critics='/reviews'
url_back_audi='/reviews?type=user'

url_critics=[]
url_audi=[]
url_mid=[]


i=0
for link in links:
  texts.append(link.text.split('\n'))
for text in texts:
  if text[0]=='[1]':
    continue
  if i%2==0:
    text_string=text[0].replace(' ','_').lower()
    name.append(text_string)
  else:
    year.append(text[0])
    if int(text[0])<2010:
      break
  i+=1

zippedList =  list(zip(name,year))

for n,y in zippedList:
  mid=url_mid.append(n+'_'+y)

for mid in url_mid:
  url_critics.append(url_front+mid+url_back_critics)
  url_audi.append(url_front+mid+url_back_audi)

zippedList =  list(zip(url_mid,url_critics,url_audi))

# for future use
dfObj = pd.DataFrame(zippedList, columns = ['Name' , 'url_critics','url_audi']) 




In [236]:
dfObj

Name  ...                                           url_audi
0                                        parasite_2019  ...  https://www.rottentomatoes.com/m/parasite_2019...
1                                  ford_v_ferrari_2019  ...  https://www.rottentomatoes.com/m/ford_v_ferrar...
2    learning_to_skateboard_in_a_warzone_(if_you're...  ...  https://www.rottentomatoes.com/m/learning_to_s...
3                           the_neighbors'_window_2019  ...  https://www.rottentomatoes.com/m/the_neighbors...
4                                    little_women_2019  ...  https://www.rottentomatoes.com/m/little_women_...
..                                                 ...  ...                                                ...
145                                   god_of_love_2010  ...  https://www.rottentomatoes.com/m/god_of_love_2...
146                                   the_wolfman_2010  ...  https://www.rottentomatoes.com/m/the_wolfman_2...
147                             strangers_no_more_2010  ...  https://www.rottentomatoes.com/m/strangers_no_...
148                                    inside_job_2010  ...  https://www.rottentomatoes.com/m/inside_job_20...
149                               the_hurt_locker_2009  ...  https://www.rottentomatoes.com/m/the_hurt_lock...

[150 rows x 3 columns]

In [0]:

def get_user_reviews():
    user_review=[]
    for url in url_audi:
      if '2019' in url:
        print(url)
        response = requests.get(url)

        soup = BeautifulSoup(response.text, "html.parser")


        # audience reviews
        audience_reviews=soup.findAll('p', attrs={'class': 'audience-reviews__review--mobile js-review-text clamp clamp-4 js-clamp'})
        if len(audience_reviews)!=0 :
          for reviews in audience_reviews:
            # print(reviews.text)
            user_review.append(reviews.text+' %% ')
    return user_review
      

In [0]:
def get_ctric_reviews():
  critic_review=[]
  review_pat = re.compile(r'<div class=\"the_review\">[;a-zA-Z\s,-.\'\/\?\[\]\":\']*</div>')


  for url in url_critics:
    if '2019' in url:
      print(url)
      response = requests.get(url)
      soup = BeautifulSoup(response.text, "html.parser")

      soup = str(soup)
      if not len(soup.split('="review_table'))==1:
        
        review_soup = soup.split('="review_table')[1].split('row review_table_row')
        review_soup.pop(0)
        review_soup = soup.split('="review_table')[1].split('row review_table_row')
        review_soup.pop(0)
        for review in review_soup:
                
                # extract review
                match = re.findall(review_pat, str(review))
                if len(match) > 0:
                    m = match[0]
                    for iden in ['<div class="the_review"> ','</div>']:
                        m = m.replace(iden,'')
                    reviews.append(m.strip('"'))
            

        # if len(audience_reviews)!=0 :
        for review in reviews:
          if review.startswith('<div class="the_review">'):
            critic_review.append(review.replace('<div class="the_review">','').replace('                                   ','').replace('\n','').replace('                                ','') + '$$')
            # print(review.replace('<div class="the_review">','').replace('                                   ','').replace('\n',''))
  return critic_review

In [239]:
critic_review=get_ctric_reviews()

https://www.rottentomatoes.com/m/parasite_2019/reviews
https://www.rottentomatoes.com/m/ford_v_ferrari_2019/reviews
https://www.rottentomatoes.com/m/learning_to_skateboard_in_a_warzone_(if_you're_a_girl)_2019/reviews
https://www.rottentomatoes.com/m/the_neighbors'_window_2019/reviews
https://www.rottentomatoes.com/m/little_women_2019/reviews
https://www.rottentomatoes.com/m/marriage_story_2019/reviews
https://www.rottentomatoes.com/m/jojo_rabbit_2019/reviews
https://www.rottentomatoes.com/m/toy_story_4_2019/reviews
https://www.rottentomatoes.com/m/joker_2019/reviews
https://www.rottentomatoes.com/m/once_upon_a_time_in_hollywood_2019/reviews
https://www.rottentomatoes.com/m/1917_2019/reviews
https://www.rottentomatoes.com/m/judy_2019/reviews
https://www.rottentomatoes.com/m/bombshell_2019/reviews
https://www.rottentomatoes.com/m/rocketman_2019/reviews
https://www.rottentomatoes.com/m/american_factory_2019/reviews
https://www.rottentomatoes.com/m/hair_love_2019/reviews


In [240]:
user_review=get_user_reviews()

https://www.rottentomatoes.com/m/parasite_2019/reviews?type=user
https://www.rottentomatoes.com/m/ford_v_ferrari_2019/reviews?type=user
https://www.rottentomatoes.com/m/learning_to_skateboard_in_a_warzone_(if_you're_a_girl)_2019/reviews?type=user
https://www.rottentomatoes.com/m/the_neighbors'_window_2019/reviews?type=user
https://www.rottentomatoes.com/m/little_women_2019/reviews?type=user
https://www.rottentomatoes.com/m/marriage_story_2019/reviews?type=user
https://www.rottentomatoes.com/m/jojo_rabbit_2019/reviews?type=user
https://www.rottentomatoes.com/m/toy_story_4_2019/reviews?type=user
https://www.rottentomatoes.com/m/joker_2019/reviews?type=user
https://www.rottentomatoes.com/m/once_upon_a_time_in_hollywood_2019/reviews?type=user
https://www.rottentomatoes.com/m/1917_2019/reviews?type=user
https://www.rottentomatoes.com/m/judy_2019/reviews?type=user
https://www.rottentomatoes.com/m/bombshell_2019/reviews?type=user
https://www.rottentomatoes.com/m/rocketman_2019/reviews?type=us

In [0]:
zippedList =  list(zip(url_mid,url_critics,url_audi,user_review,critic_review))
dfObj = pd.DataFrame(zippedList, columns = ['Name' , 'url_critics','url_audi','user_review','critic_review']) 

In [242]:
dfObj['critic_review'][0]

" Do yourself a favor and catch La La Land. It's a necessary reminder that romance, triumph, and hope don't just exist in the movies.$$"

In [0]:
dfObj.to_excel('test.xlsx')

In [0]:
def new_get_user_reviews(url):
    user_review=[]
  
    print(url)
    response = requests.get(url)
    if response.status_code ==200:
      soup = BeautifulSoup(response.text, "html.parser")
      # audience reviews
      audience_reviews=soup.findAll('p', attrs={'class': 'audience-reviews__review--mobile js-review-text clamp clamp-4 js-clamp'})
      if len(audience_reviews)!=0 :
        for reviews in audience_reviews:
          # print(reviews.text)
          user_review.append(reviews.text+' %% ')
    return user_review






def new_get_ctric_reviews(url):
  critic_review=[]
  review_pat = re.compile(r'<div class=\"the_review\">[;a-zA-Z\s,-.\'\/\?\[\]\":\']*</div>')

  print(url)
  print('list£££££££££££££££')
  print(critic_review)
  response = requests.get(url)
  if response.status_code ==200:
    soup = BeautifulSoup(response.text, "html.parser")

    soup = str(soup)
    if not len(soup.split('="review_table'))==1:
      
      review_soup = soup.split('="review_table')[1].split('row review_table_row')
      review_soup.pop(0)
      review_soup = soup.split('="review_table')[1].split('row review_table_row')
      review_soup.pop(0)
      for review in review_soup:
              
              # extract review
              match = re.findall(review_pat, str(review))
              if len(match) > 0:
                  m = match[0]
                  for iden in ['<div class="the_review"> ','</div>']:
                      m = m.replace(iden,'')
                  reviews.append(m.strip('"'))
          

      # if len(audience_reviews)!=0 :
      for review in reviews:
        if review.startswith('<div class="the_review">'):
          critic_review.append(review.replace('<div class="the_review">','').replace('                                   ','').replace('\n','').replace('                                ','') + '$$')
        # print(review.replace('<div class="the_review">','').replace('                                   ','').replace('\n',''))
  return critic_review

In [0]:

def get_review_year(year):
  for user_url,critic_url in zip(url_audi,url_critics):
    if year in user_url:
      print(new_get_user_reviews(user_url))
      print(new_get_ctric_reviews(critic_url))
     


In [255]:
get_review_year('2017')

https://www.rottentomatoes.com/m/the_shape_of_water_2017/reviews?type=user
["A great and brilliant love story, combined with Del Toro's direction, the script he co-wrote with Taylor, the performances of the cast, Desplat's score, Laustsen's cinematography, Wolinsky's editing, Austerberry's production design, Melvin and Vieau's set decoration, Sequeira's costume design, action sequences and visual effects, The Shape Of Water is a brilliant and entertaining movie!!! %% ", "It's got it's moment, but in the end, it's too much of a pastiche of things we've seen before. The hyped up style gets a bit tiresome after a while. In general, I think the whole concept would have worked better as a short film. On the plus side, the CGI is widely convincing and the acting is impeccable. %% ", 'Great movie with the new interesting and different storyline %% ', "It's Friday Friday Gotta Ge Down On Friday, Dead memes are cool man. Harambe. Also this movie sucks. It truly is the fish banging movie. %% ", 